In [7]:
import matplotlib.pyplot as plt
import networkx as nx
import random
import json
import os

In [8]:
def hierarchy_pos(G,
                  root=None,
                  width=1.,
                  vert_gap=0.2,
                  vert_loc=0,
                  xcenter=0.5):
    '''
    From Joel's answer at https://stackoverflow.com/a/29597209/2966723.  
    Licensed under Creative Commons Attribution-Share Alike 
    
    If the graph is a tree this will return the positions to plot this in a 
    hierarchical layout.
    
    G: the graph (must be a tree)
    
    root: the root node of current branch 
    - if the tree is directed and this is not given, 
      the root will be found and used
    - if the tree is directed and this is given, then 
      the positions will be just for the descendants of this node.
    - if the tree is undirected and not given, 
      then a random choice will be used.
    
    width: horizontal space allocated for this branch - avoids overlap with other branches
    
    vert_gap: gap between levels of hierarchy
    
    vert_loc: vertical location of root
    
    xcenter: horizontal location of root
    '''
    if not nx.is_tree(G):
        raise TypeError(
            'cannot use hierarchy_pos on a graph that is not a tree')

    if root is None:
        if isinstance(G, nx.DiGraph):
            root = next(iter(nx.topological_sort(
                G)))  #allows back compatibility with nx version 1.11
        else:
            root = random.choice(list(G.nodes))

    def _hierarchy_pos(G,
                       root,
                       width=1.,
                       vert_gap=0.2,
                       vert_loc=0,
                       xcenter=0.5,
                       pos=None,
                       parent=None):
        '''
        see hierarchy_pos docstring for most arguments

        pos: a dict saying where all nodes go if they have been assigned
        parent: parent of this branch. - only affects it if non-directed

        '''

        if pos is None:
            pos = {root: (xcenter, vert_loc)}
        else:
            pos[root] = (xcenter, vert_loc)
        children = list(G.neighbors(root))
        if not isinstance(G, nx.DiGraph) and parent is not None:
            children.remove(parent)
        if len(children) != 0:
            dx = width / len(children)
            nextx = xcenter - width / 2 - dx / 2
            for child in children:
                nextx += dx
                pos = _hierarchy_pos(G,
                                     child,
                                     width=dx,
                                     vert_gap=vert_gap,
                                     vert_loc=vert_loc - vert_gap,
                                     xcenter=nextx,
                                     pos=pos,
                                     parent=root)
        return pos

    return _hierarchy_pos(G, root, width, vert_gap, vert_loc, xcenter)

In [9]:
# file_path = "../examples/Knapsack/logging/06-26-2022 09:55:20 RPXLBG.log"
file_path = "../examples/Gomoku/logging/06-26-2022 20:48:07 UPJMUD.log"

with open(file_path) as f:
    origin_data = f.readlines()
file_name = os.path.basename(file_path).split('.')[0]

In [10]:
node_dict = {}

for i, e in enumerate(origin_data):
    if i == 0:
        continue
    msg = json.loads(e)["message"]
    node_dict[msg[6:18]] = {
        "parent": msg[29:41],
        "msg": msg.split("visits:")[1].split(" |")[0]
    }

print(len(origin_data))

29419


In [11]:
T = nx.Graph()
property_dict = {}

for i, e in enumerate(node_dict):
    if i == 0:
        root = e
        T.add_node(e, msg=node_dict[e]["msg"])
        continue
    property_dict[e] = (e, node_dict[e]["msg"])

    T.add_node(e, msg=node_dict[e]["msg"])
    # T.add_node(e)
    T.add_edge(e, node_dict[e]["parent"])

In [12]:
plt.figure(figsize=(240, 40), dpi=72)
nx.draw(T,
        pos=hierarchy_pos(T, root=root, width=1e8),
        node_size=10,
        with_labels=False,
        labels=property_dict)
plt.savefig("data/{}.png".format(file_name), format="PNG")
plt.show()